$$
\def\CC{\bf C}
\def\QQ{\bf Q}
\def\RR{\bf R}
\def\ZZ{\bf Z}
\def\NN{\bf N}
$$
# Les décorateurs en Sage (et en Python)

Permettent de modifier des fonctions ou des variables sans trop d'effort!

Initialement, les décorateurs comme @static\_method ont été introduits dans Python pour simplifier la syntaxe : <https://www.python.org/dev/peps/pep-0318/#motivation>

## @cached\_function et @cached\_method

Ne fonctionne que dans Sage, pas dans Python. Le but est de mémoriser les résultats déjà obtenus (sans effort!). Ça permet d'améliorer (parfois) la complexité du code s'il y a plusieurs fois les mêmes appels. Tout ce qu'il y a à faire est ajouter le décorateur devant la fonction.

### Différence entre méthode et fonction :

Une méthode est dans une classe et est rattachée à un objet, une fonction n'est pas dans une classe.

In [ ]:
# De façon naïve
def Fibonacci(n):  # retourne le n-ième terme de la suite de Fibonacci
    if n == 0 or n == 1:
        return 1
    return Fibonacci(n-1) + Fibonacci(n-2)

In [ ]:
%time Fibonacci(33)

CPU times: user 5.83 s, sys: 4.13 ms, total: 5.84 s
Wall time: 5.84 s
5702887

In [ ]:
@cached_function
def Fibonacci(n):  # retourne le n-ième terme de la suite de Fibonacci
    if n == 0 or n == 1:
        return 1
    return Fibonacci(n-1) + Fibonacci(n-2)

In [ ]:
%time Fibonacci(33)

CPU times: user 399 µs, sys: 12 µs, total: 411 µs
Wall time: 383 µs
5702887

In [ ]:
%time Fibonacci(330)

CPU times: user 2.45 ms, sys: 18 µs, total: 2.47 ms
Wall time: 2.18 ms
668996615388005031531000081241745415306766517246774551964595292186469

Ce n'est pas toujours efficace... Il faut donc parfois vraiment changer son code!

In [ ]:
%time Fibonacci(1000)

---------------------------------------------------------------------------
RuntimeError                              Traceback (most recent call last)
<ipython-input-6-b6ed43b201c3> in <module>()
----> 1 get_ipython().magic(u'time Fibonacci(1000)')

/home/nadia/SageMath/local/lib/python2.7/site-packages/IPython/core/interactiveshell.pyc in magic(self, arg_s)
   2158         magic_name, _, magic_arg_s = arg_s.partition(' ')
   2159         magic_name = magic_name.lstrip(prefilter.ESC_MAGIC)
-> 2160         return self.run_line_magic(magic_name, magic_arg_s)
   2161 
   2162     #-------------------------------------------------------------------------
/home/nadia/SageMath/local/lib/python2.7/site-packages/IPython/core/interactiveshell.pyc in run_line_magic(self, magic_name, line)
   2079                 kwargs['local_ns'] = sys._getframe(stack_depth).f_locals
   2080             with self.builtin_trap:
-> 2081                 result = fn(*args,**kwargs)
   2082             return resul

Ce problème peut être réglé en lui faisant faire les calculs dans le bon ordre :

In [ ]:
%%time
for i in range(10000):
    Fibonacci(i)
Fibonacci(10000)

CPU times: user 64.4 ms, sys: 815 µs, total: 65.2 ms
Wall time: 61 ms

## @interact

Permet à l'utilisateur de changer visuellement les paramètres d'une fonction. *Dans l'atelier, la spécialiste est Odile!*

In [ ]:
# sin(n*x)
var('x')
@interact
def _(n=range(1, 11)):
    f = sin(n*x)
    show(plot(f, x, -2*pi, 2*pi))

In [ ]:
@interact
def _(n=(5..100)):
    Poset(([1..n], lambda x, y: y%x == 0) ).show()

Pour plus d'exemples des possibilités de @interact, vous pouvez consulter le wiki de Sage : <https://wiki.sagemath.org/interact>

## @parallel

Le parallélisme ([https://fr.wikipedia.org/wiki/Parall%C3%A9lisme\\\_(informatique)](https://fr.wikipedia.org/wiki/Parall%C3%A9lisme\_(informatique))) s'effectue lorsqu'un algorthme est exécuté simultanément sur plusieurs processeurs. Par exemple, si on a beaucoup d'exemples similaires et indépendants à tester, on peut les vérifier en même temps.

Pour que ça fonctionne, il faut faire une fonction décorée par @parallel(ncpus=N) (où N est le nombre de processeurs à utiliser) qui prend un paramètre. Lorsqu'on appelle cette fonction, on lui soumet une liste de paramètres. Le parallélisme gère la multiplication des processus.

#### Nombre chromatique d'un grand nombre de graphes

In [ ]:
G = [graphs.RandomGNP(25, 0.5) for i in range(10)]

Sans le parallélisme.

In [ ]:
def count_graphs_with_chi_less_than(i, L):
    p = 0
    for g in G:
        if g.chromatic_number() < i:
            p += 1
    return p

%time count_graphs_with_chi_less_than(8, G)

CPU times: user 29.4 s, sys: 0 ns, total: 29.4 s
Wall time: 29.4 s
10

Avec parallélisme.

In [ ]:
@parallel(ncpus=4)
def chromatic_number(graph):
    return graph.chromatic_number()

In [ ]:
def count_graphs_with_chi_less_than(i, G):
    counter = 0
    for arg,res in chromatic_number(G):
        if res < i:
            counter += 1
    return counter

In [ ]:
%time count_graphs_with_chi_less_than(8, G)

CPU times: user 27 ms, sys: 84.3 ms, total: 111 ms
Wall time: 12.9 s
10

#### La conjecture de Goldbach

Avec parallélisme.

In [ ]:
@parallel(ncpus=4)
def is_sum_of_two_primes(n):
    p = 0
    while p < n/2 + 1:
        if (n-p).is_prime():
            return True
        p = next_prime(p)
    return False

In [ ]:
def Goldbach_interval(m, n):  # m doit être pair, au moins 2
    for (arg, _),res in is_sum_of_two_primes(range(m, n+1, 2)):
        # print arg[0]  # Si on veut voir que les valeurs ne sont pas nécessairement calculées dans l'ordre
        if not res:
            print "counterexample!", arg
            return False
    return True

In [ ]:
%time Goldbach_interval(10**120, 10**120+200)

CPU times: user 143 ms, sys: 924 ms, total: 1.07 s
Wall time: 13 s
True

Sans le parallélisme.

In [ ]:
def is_sum_of_two_primes(n):
    p = 0
    # print n  # Les valeurs de n s'affichent nécessairement dans l'ordre si on les appelle dans l'ordre (ex. range)
    while p < n/2 + 1:
        if (n-p).is_prime():
            return True
        p = next_prime(p)
    return False

In [ ]:
def Goldbach_interval(m, n):  # m doit être pair, au moins 2
    for i in range(m, n+1, 2):
        if not is_sum_of_two_primes(n):
            print "counterexample!", n
            return False
    return True

In [ ]:
%time Goldbach_interval(10**120, 10**120+200)

CPU times: user 24 s, sys: 20.1 ms, total: 24 s
Wall time: 24 s
True

## @lazy\_attribute

@lazy\_attribute pour un objet est un attribut qui ne sera calculé qu'une seule fois, lorsqu'on y accède. Ça évite de le calculer lors de la construction de l'objet si ce n'est pas nécessaire.

In [ ]:
class A(object):
    def __init__(self):
        self.a = is_prime(2^10000000-1) # just to have some data to calculate from

    @lazy_attribute
    def x(self):
        print("Cette fois, je fais les calculs")
        return self.a + 1

In [ ]:
a = A()
a.x

Cette fois, je fais les calculs
1

In [ ]:
a.x

1

In [ ]:
a = A()
print a.__dict__
a.x
print a.__dict__
a.x  # rien ne se passe, car x est déjà dans le dictionnaire et que le constructeur est paresseux

{'a': False}
Cette fois, je fais les calculs
{'a': False, 'x': 1}
1

In [ ]:
#sans lazy_attribute
class A(object):
    def __init__(self):
        self.a = is_prime(2^10000000-1) # just to have some data to calculate from
        self.x = self.a + 1
        print "J'ai fait les calculs pour x"

    #def x(self):
    #    print("Cette fois, je fais les calculs")
    #    return self.a + 1

In [ ]:
a = A()
a.x

J'ai fait les calculs pour x
1

In [ ]:
a = A()

J'ai fait les calculs pour x

In [ ]:
a.x

1

## Décorateurs personalisés

On peut faire nos propres décorateurs! Pour en savoir plus : \[<https://doc.sagemath.org/html/en/reference/misc/sage/misc/decorators.html>\]

### Un décorateur qui sert surtout à décorer... avec des print.

In [ ]:
var('n')
assume(n, 'integer')
n = 3

from sage.misc.decorators import decorator_defaults
@decorator_defaults
def blabla(f,*args):
    print "Bonjour!"
    return f

@blabla
def sq(n=3):
    return n^2

Bonjour!

In [ ]:
sq(3)

9

In [ ]:
@blabla
def cube(n=5):
    return n^3

Bonjour!

In [ ]:
@blabla
def _(n=5):
    return n^3

Bonjour!

In [ ]:
print sq(7)
print cube(5)

49
125

In [ ]:
sage: f = specialize(5)(lambda x, y: x+y)
sage: f(10)
15
sage: f(5)
10
@specialize("Bon Voyage")
def greet(greeting, name):
    print("{0}, {1}!".format(greeting, name))

In [ ]:
greet(name = 'Javert')

Bon Voyage, Javert!

In [ ]:
greet("Mélodie")

Bon Voyage, Mélodie!

### Un décorateur qui modifie la réponse

On peut même en faire qui modifie ce que la fonction fait. Faites gaffe aux décorateurs que vous ne connaissez pas!

In [ ]:
def piege(f):
    @sage_wraps(f)  # pour que la fonction soit modifiée
    def new_f(x):
        return f(x)*f(x)
    return new_f

@piege
def id(x):
    return x

@piege
def factorize(n):
    return n.factor()

In [ ]:
id(5)

25

In [ ]:
factorize(343)

7^6

## Experimental

Enfin, un décorateur qu'on peut aussi retrouver dans le code de Sage.

In [ ]:
from sage.misc.superseded import experimental
@experimental(13215)
def is_something(n):
    return True

In [ ]:
is_something(2)

/home/nadia/SageMath/local/lib/python2.7/site-packages/sage/repl/ipython_kernel/__main__.py:1: FutureWarning: This class/method/function is marked as experimental. It, its functionality or its interface might change without a formal deprecation.
See http://trac.sagemath.org/13215 for details.
  from ipykernel.kernelapp import IPKernelApp
True

In [ ]:
# L'avertissement ne s'affiche qu'une fois
is_something(3)

True

## Références :

-   En Python : <https://www.python.org/dev/peps/pep-0318/>
-   En Sage : <https://doc.sagemath.org/html/en/reference/misc/sage/misc/decorators.html>